## Librerías

In [1]:
import pandas as pd
from shapely import wkt
from shapely.ops import transform
import pyproj
from functools import partial
import folium

# Limpieza parques y jardines

## Filtrar por tamaño de "parcela"

###### No ejecutar mas

In [2]:
df = pd.read_csv('parques_y_jardines.csv')

df['geometry'] = df['geometry'].apply(wkt.loads)

def project_geom(geom):
    project = partial(
        pyproj.transform,
        pyproj.Proj(init='epsg:4326'),  
        pyproj.Proj(init='epsg:3857'))  
    return transform(project, geom)

df['area'] = df['geometry'].apply(lambda geom: project_geom(geom).area)

umbral_area = 100  
df_filtrado = df[df['area'] > umbral_area]

df_filtrado.to_csv('parques_y_jardines.csv', index=False)

df_filtrado.shape[0]

c:\Users\memol\AppData\Local\Programs\Python\Python311\Lib\site-packages\pyproj\crs\crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
c:\Users\memol\AppData\Local\Programs\Python\Python311\Lib\site-packages\pyproj\crs\crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
c:\Users\memol\AppData\Local\Programs\Python\Python311\Lib\site-packages\shapely\ops.py:274: FutureWarning: This function is deprecated. See: https://pyproj4.gi

3819

### Mapear las parcelas

###### No ejecutar mas

In [3]:
df_filtrado = pd.read_csv('parques_y_jardines.csv')

df_filtrado['geometry'] = df_filtrado['geometry'].apply(wkt.loads)

if 'etiqueta' not in df_filtrado.columns:
    df_filtrado['etiqueta'] = range(1, len(df_filtrado) + 1)

mapa = folium.Map(location=[42.3439, -3.6969], zoom_start=13)

for parque, row in df_filtrado.iterrows():
    popup_text = f"ID: {row['etiqueta']} - {row.get('name', 'Sin nombre')} - Área: {row['area']} m²"
    if row['geometry'].geom_type == 'Point':
        folium.Marker(
            location=[row['geometry'].y, row['geometry'].x],
            popup=popup_text
        ).add_to(mapa)
        
    elif row['geometry'].geom_type == 'Polygon':
        folium.Polygon(
            locations=[(point[1], point[0]) for point in row['geometry'].exterior.coords],
            popup=popup_text,
            color='#3186cc',  
            fill=True,
            fill_color='#3186cc', 
            fill_opacity=0.4  
        ).add_to(mapa)

mapa.save('mapa_parques_y_jardines.html')

df_filtrado.to_csv('parques_y_jardines.csv', index=False)

### Limpieza visual entre el mapa de folium y los datos del csv

#### Repetir cuantas veces necesitemos

In [ ]:
df_filtrado = pd.read_csv('parques_y_jardines.csv')

In [19]:
rangos_a_eliminar = []

numeros_especificos = []

In [20]:
# Convertir los rangos en una lista de números
numeros_a_eliminar = []
for rango in rangos_a_eliminar:
    numeros_a_eliminar.extend(range(rango[0], rango[1] + 1))

numeros_a_eliminar.extend(numeros_especificos)

df_filtrado = df_filtrado[~df_filtrado['etiqueta'].isin(numeros_a_eliminar)]

df_filtrado.to_csv('parques_y_jardines_filtrado.csv', index=False)


#### Mapear el resultado final

In [17]:
df_filtrado_actualizado = pd.read_csv('parques_y_jardines_filtrado.csv')

df_filtrado_actualizado['geometry'] = df_filtrado_actualizado['geometry'].apply(wkt.loads)

mapa_actualizado = folium.Map(location=[42.3439, -3.6969], zoom_start=13)

for _, row in df_filtrado_actualizado.iterrows():
    popup_text = f"ID: {row['etiqueta']} - {row.get('name', 'Sin nombre')} - Área: {row['area']} m²"
    if row['geometry'].geom_type == 'Point':
        folium.Marker(
            location=[row['geometry'].y, row['geometry'].x],
            popup=popup_text
        ).add_to(mapa_actualizado)
    elif row['geometry'].geom_type == 'Polygon':
        folium.Polygon(
            locations=[(point[1], point[0]) for point in row['geometry'].exterior.coords],
            popup=popup_text,
            color='#3186cc',
            fill=True,
            fill_color='#3186cc',
            fill_opacity=0.7
        ).add_to(mapa_actualizado)

mapa_actualizado.save('mapa_parques_y_jardines_actualizado.html')


##### Repetimos limpieza